In [78]:
# Utilities
from pathlib import Path
import os, sys
import subprocess as sp
from functools import partial

# Data
import pandas as pd
import numpy as np

# Brain 
import nibabel as nb
from nibabel.freesurfer.io import read_annot, read_morph_data, read_geometry
#import cortex
#import src.mesh_laplace_sulci
import src.freesurfer_utils as sfu


import gdist
import pygeodesic.geodesic as geodesic

# Plotting
#from mpl_toolkits import mplot3d
# from mpl_toolkits.mplot3d import Axes3D
#%matplotlib inline
%matplotlib widget
import matplotlib.pyplot as plt

#from src.utility_funcs import mris_convert_command

# Meshes
import igl
# import meshplot 
import trimesh as tm
from src.surface_funcs import *

## Desired functions

1. Get ROI: using four boundary sulci, get all faces and vertices within them  
2. Get centroid: find the centroid of a label
3. Get crowns: find the gyral crowns (or pits) within a label
4. Autosegment: surface simplification for data-driven segmentation of labels
5. Geodesic distance: geodesic distance AND path between sets of vertices

Idea for 1:
- Get boundary vertices  
- draw geodesic path among boundary vertices  
- Geodesic path among edges i.e. superior edge of anterior -> anterior edge of superior  
- being at superior of anterior, move one edge posterior and inferior  
- if target vertex is not in boundary vertices, add face to label  
- if target vertex is in boundary vertices, select other edge ~~ which edge? spiral through  
  - before adding check all three adjacent triangles  
  - plan to go to next triangle which has border with added vertex  

In [4]:

def get_faces_from_vertices(faces : np.array, label_ind : np.array):
    """
    Takes a list of faces and label indices
    Returns the faces that contain the indices

    INPUT:
    faces: array of faces composed of 3 points
    label_ind: array of indices of points in the label (first colum of label file; 0 index in read_label)

    OUTPUT:
    label_faces: array of faces that contain the points in the label
    """
    all_label_faces = []
    for face in faces:
        for point_index in face:
            if point_index in label_ind:
                all_label_faces.append(list(face))
    return np.array(all_label_faces)

def get_boundary_faces(all_faces : np.array, label_ind : np.array):
    """
    For a given label, find the faces that are on the boundary of the label by finding vertices
    that only appear twice in the array of faces (all interior vertices will appear 3 or more times)

    INPUT:
        all_faces : np.array - array of faces from the mesh
        label_ind : np.array - array of vertices that are in the label, first column in freesurfer .label file
    OUTPUT:
        boundary_faces : np.array - array of faces that are on the boundary of the label
    """
    # Find the unique faces of a label
    faces_in_label = get_faces_from_vertices(all_faces, label_ind)
    unique_entry, count = np.unique(faces_in_label, return_counts=True)
    # Get the nodes that only appear once
    boundary_nodes = unique_entry[count <= 6]
    # Get the faces that include the boundary nodes
    boundary_faces = get_faces_from_vertices(all_faces, boundary_nodes)
    return boundary_faces


def read_label(label_name):
    """
    Reads a freesurfer-style .label file (5 columns)
    
    Parameters
    ----------
    label_name: str 
    
    Returns 
    -------
    vertices: index of the vertex in the label np.array [n_vertices] 
    RAS_coords: columns are the X,Y,Z RAS coords associated with vertex number in the label, np.array [n_vertices, 3] 
    
    """
    
    # read label file, excluding first two lines of descriptor 
    df_label = pd.read_csv(label_name,skiprows=[0,1],header=None,names=['vertex','x_ras','y_ras','z_ras','stat'],delimiter='\s+')
    
    vertices = np.array(df_label.vertex) 
    RAS_coords = np.empty(shape = (vertices.shape[0], 3))
    RAS_coords[:,0] = df_label.x_ras
    RAS_coords[:,1] = df_label.y_ras
    RAS_coords[:,2] = df_label.z_ras
    
    return vertices, RAS_coords


def write_label(label_name : str, label_faces : np.array, verts : np.array, hemi : str, subject : str, subjects_dir : str, surface_type : str = 'white'):
    """
    Write a freesurfer label file 

    INPUT:
    label_name : str - name of label for save file
    label_faces : np.array - array of faces for label
    verts : np.array - array of all vertices in subject hemi; if None, will read in subject hemisphere from /surf/ file
    hemi : str - hemisphere of label
    subject : str - subject ID
    subjects_dir : str - filepath to freesurfer subjects directory
    surface_type : str - surface type for label (default = 'white')

    OUTPUT:
    writes label file to subject label directory
    """
    
    assert os.path.exists(subjects_dir), f'{subjects_dir} does not exist'
    subject_dir = f"{subjects_dir}/{subject}"
    assert os.path.exists(subject_dir), f'{subject_dir} does not exist'


    label_ind = np.unique(label_faces)
    if verts is None:
        hemi_surf = f"{subjects_dir}/{subject}/surf/{hemi}.{surface_type}"
        verts, faces = read_geometry(hemi_surf)

    label_verts = verts[label_ind]

    label_filename = f"{subjects_dir}/{subject}/label/{hemi}.{label_name}.label"

    with open(label_filename, 'w') as f:
        f.write(f"#!ascii label , from subject {subject} vox2ras=TkReg coords={surface_type} \n")
        f.write(f"{len(label_ind)} \n")
        for i, ind in enumerate(label_ind):
            f.write(f"{ind} {np.round(label_verts[i][0], decimals=3)} {np.round(label_verts[i][1], decimals=3)} {np.round(label_verts[i][2], decimals=3)} 0.0000000000 \n")



In [7]:
# filepath = '/Users/benparker/Desktop/cnl/subjects/100307/surf/lh.pial'

# mris_convert_command(filepath, custom_filename='mris_convert')

In [5]:
subjects_dir = '/Users/sathishkumar/Desktop/chimp_subjects.nosync'
labels = ['csts-1', 'csts-3']
sub = 'c05'
hemi = 'lh'
outdir = '/Users/sathishkumar/Desktop/chimp_subjects.nosync/results'

In [8]:
subjects_dir = '/Users/benparker/Desktop/cnl/subjects'
labels = ['POS','MCGS']
sub = '100307'
hemi = 'lh'
outdir = '/Users/benparker/Desktop/cnl/CNL_scalpel/results'

#getDistMatrix(subjects_dir,labels,sub,hemi,outdir, fmri_prep=False)

In [6]:
highres_surface = f'{subjects_dir}/{sub}/surf/{hemi}.pial'
    
 
giidata = nb.freesurfer.read_geometry(highres_surface)
points, faces = giidata[0], giidata[1]

label_ind = nb.freesurfer.read_label('/Users/sathishkumar/Desktop/chimp_subjects.nosync/c05/label/lh.csts-1.label')

# ben path: /Users/benparker/Desktop/cnl/subjects/100307/label/rh.MCGS.label
# rey path: /Users/sathishkumar/Desktop/chimp_subjects/c05/label/lh.csts-1.label

label_points = points[label_ind]
label_faces = faces[label_ind]


In [ ]:
unique_entry, count = np.unique(label_faces, return_counts=True)


In [ ]:
adjacency = mesh_to_adjacency(faces, points)
adacent_nodes = adjacenct_nodes(adjacency, 0)

    

    

In [34]:
label_faces

array([[18212, 18225, 18213],
       [18218, 19159, 19175],
       [18226, 18243, 18227],
       [18233, 18249, 18234],
       [18704, 18720, 18719],
       [18705, 18706, 18721],
       [18705, 18721, 18720],
       [18706, 19722, 18721],
       [18712, 19738, 19728],
       [18714, 19732, 18715],
       [19733, 18715, 19732],
       [18715, 19733, 18716],
       [18719, 18720, 18732],
       [18719, 18732, 18731],
       [18720, 18721, 18733],
       [18720, 18733, 18732],
       [19742, 18726, 19741],
       [18726, 19742, 18727],
       [19743, 18727, 19742],
       [19764, 18747, 19748],
       [19181, 19195, 19196],
       [19181, 19196, 19182],
       [19181, 20150, 20164],
       [19186, 20155, 20168],
       [19186, 20168, 19199],
       [19187, 20156, 20157],
       [19190, 20172, 19202],
       [19191, 19203, 19204],
       [19191, 19204, 19192],
       [19196, 20165, 20175],
       [19196, 20175, 19205],
       [19197, 19207, 20176],
       [19202, 20173, 19203],
       [19

In [7]:
def find_shortest_path_in_mesh(coordinates, triangles, source_index, target_index):
    # Create a graph from the mesh
    G = create_graph_from_mesh(coordinates, triangles)

    # Find the shortest path
    path = nx.shortest_path(G, source=source_index, target=target_index)

    return path

#just added this here for now!

In [8]:
## in theory this should work, but I'm not sure that I'm indexing the label correctly. Plotting this can clarify
def find_boundary_nodes(all_faces : np.ndarray, label_ind : np.ndarray):
    """ 
    Find the boundary nodes of a label by isolating faces who include a node that onle appears in one face.
    
    INPUT:
    all_faces : np.array - an array of all the faces in the mesh
    label_ind : np.array - an array of the indices of the label

    OUTPUT:
    boundary_faces : np.array - an array of the boundary faces

    """
    # Get the unique nodes in the label
    unique_entry, count = np.unique(all_faces[label_ind], return_counts=True)
    # Get the nodes that only appear once
    boundary_nodes = unique_entry[count == 1]
    return boundary_nodes

    

In [ ]:
# test_sub = ScalpelSurface(subject_filepath='~/Desktop/cnl/subjects/100307')
# boundary_dict = test_sub.get_boundary(anterior_label='MCGS', posterior_label='POS', 
#                                       inferior_label='2', superior_label='MCGS', hemi='lh')


        
        

In [ ]:
# post_nodes = boundary_dict['posterior'][0]
# post_nodes

# post_points = boundary_dict['posterior'][1]
# post_points[:15]


In [ ]:
# np.isin(np.round(np.take(points, post_nodes, axis=0), decimals=3), [-30.882, -15.272, -12.153]).sum()

In [ ]:
# label_annot = nb.freesurfer.read_annot('/Users/benparker/Desktop/cnl/subjects/100307/label/lh.PFC_annot.annot')

# for id in np.unique(label_annot[0]):
#     print('id = %d, sum = %d'%(id, (label_annot[0] == id).sum()))

## Mesh traversal

In [9]:
subjects_dir = '/Users/sathishkumar/Desktop/neurocluster/NH_Primates/chimp_data'
labels = ['POS','MCGS']
sub = 'c05'
hemi = 'rh'
#outdir = '/Users/benparker/Desktop/cnl/CNL_scalpel/results'

#getDistMatrix(subjects_dir,labels,sub,hemi,outdir, fmri_prep=False)

highres_surface = f'{subjects_dir}/{sub}/surf/{hemi}.pial'
    
 
giidata = nb.freesurfer.read_geometry(highres_surface)
points, faces = giidata[0], giidata[1]

### Do not use nibabel to read_labels because only returns vertices, not coordinates
#DONT_label_ind = nb.freesurfer.read_label('/Users/benparker/Desktop/cnl/subjects/100307/label/rh.POS.label')


label_ind, label_RAS = read_label(f'{subjects_dir}/{sub}/label/rh.csts-1.label')



In [39]:
label_ind

array([33984, 33994, 33995, 33996, 33997, 34006, 34007, 34008, 34009,
       34019, 34020, 34021, 34962, 34980, 34992, 34993, 35001, 35002,
       35003, 35011, 35012, 35013, 35021, 35022, 35023, 35024, 35034,
       35035, 35036, 35037, 35038, 35053, 35054, 35055, 35068, 35069,
       35070, 35080, 36025, 36035, 36036, 36044, 36045, 36055, 36056,
       36063, 36070, 36071, 36081, 36082, 36083, 36095, 36096, 36097,
       36109, 36110, 36111, 36112, 37110, 37111, 37116, 37117, 37121,
       37130, 37131, 37140, 37141, 37150, 37151, 37165, 37175, 37176,
       37185, 37186, 38129, 38130, 38148, 38149, 38150, 38161, 38162,
       38163, 38164, 38167, 38168, 38169, 38170, 38172, 38173, 38174,
       38176, 38177, 38181, 38182, 38187, 38188, 38198, 38199, 38211,
       38219, 38220, 38228, 38229, 39149, 39150, 39161, 39162, 39163,
       39164, 39165, 39166, 39167, 39168, 39169, 39170, 39176, 39177,
       39178, 39179, 39180, 39181, 39182, 39183, 39184, 39185, 39186,
       39187, 39194,

In [ ]:
faces

array([[     0,      1,      3],
       [     4,      3,      1],
       [     0,     44,      1],
       ...,
       [129160, 129996, 129163],
       [129456, 129996, 129155],
       [129456, 129747, 129996]], dtype='>i4')

In [ ]:
label_RAS

array([[ 29.247, -79.741,  -7.36 ],
       [ 28.847, -80.007,  -7.222],
       [ 28.063, -80.   ,  -7.036],
       ...,
       [  6.207,  78.346, -34.479],
       [  6.637,  77.998, -34.32 ],
       [  7.032,  78.145, -33.883]])

In [40]:
# From all faces in giidata, get the faces in the label
label_faces = get_faces_from_vertices(faces, label_ind)

In [41]:
label_faces

array([[33995, 33982, 33093],
       [33994, 33092, 33993],
       [33092, 33994, 33093],
       ...,
       [42610, 42611, 42626],
       [42627, 42626, 42611],
       [42611, 42612, 42627]], dtype=int32)

In an alternate plotting library (trimesh)

In [77]:


mesh = tm.Trimesh(vertices= points, faces = faces)
mesh.show()

In [ ]:
points

array([[ 29.98126411, -81.2410965 ,  -7.96126509],
       [ 29.53573036, -81.38262177,  -7.82315588],
       [ 28.77490234, -81.57066345,  -7.63856936],
       ...,
       [  5.55454922,  79.7095108 , -37.41462326],
       [  6.43620586,  79.49263763, -37.41100311],
       [  7.28207636,  79.7323761 , -37.05001068]])

In [ ]:
faces

array([[     0,      1,      3],
       [     4,      3,      1],
       [     0,     44,      1],
       ...,
       [129160, 129996, 129163],
       [129456, 129996, 129155],
       [129456, 129747, 129996]], dtype='>i4')

In [ ]:
mesh.show()

In [ ]:

label_mesh = tm.Trimesh(vertices= points, faces = label_faces)
label_mesh.show()

Check to see the boundary identified by our functions

TODO get shortest path between landmarks

Start in VTC connecting OTS and CoS, generalize from there to PFC PMC

In [16]:
pos_boundary = get_boundary_faces(faces, label_ind)
boundary_mesh = tm.Trimesh(vertices= points, faces = pos_boundary)
boundary_mesh.show()

Seems to be identifying something close to the border. Might have some gaps though. 

Lets save it as a freesurfer label and write it
    - Looks good  
    - Actually seems to be the border immediately around the POS label
      
        
          
Now, what if we apply the BFS search to the boundary created by our pos_boundary. It should return the same label


In [43]:

def find_vert_inside(adjacency_matrix: np.array, vert : int, all_verts : np.array, label_verts : np.array, direction : str = 'anterior'):
        """ 
        Finds the first vertex on a graph inside of a boundary, according to a direction. 
        i.e. 'anterior' will find the first anterior vertex inside the <vert> given

        INPUT:
        adjacency_matrix: np.array - adjacency matrix of a mesh provided by mesh_to_adjacency()
        vert: int - index of vertex to find adjacent nodes
        all_verts: np.array - array of all vertices in mesh
        label_verts: np.array - array of vertices in boundary
        direction: str - direction to search for first point inside boundary

        OUTPUT:
        first_vert_index: int - index of first vert inside boundary
        """

        ## Recursively check for first point anterior to boundary
        adjacent_points = adjacenct_nodes(adjacency_matrix, vert)

        if direction == 'anterior':
            dir_idx = 1
            dir_function = np.min
        if direction == 'posterior':
            dir_idx = 1
            dir_function = np.max
        if direction == 'inferior':
            dir_idx = 2
            dir_function = np.min
        if direction == 'superior':
            dir_idx = 2
            dir_function = np.max                  
        all_verts_in_direction = np.array([vert_i for vert_i in np.take(all_verts, adjacent_points, axis=0)[dir_idx]]).flatten()
        first_point = dir_function(all_verts_in_direction)
        if first_point in label_verts:
            find_vert_inside(first_point)
        else:
            ## Base 
            ### Return index and value
            first_vert_index = np.where(all_verts[:, dir_idx] == first_point)[0][0] 
            return first_vert_index 
        
def find_edge_vert(label_RAS: np.array, label_ind: np.array, direction: str):
    """
    Finds the vertex on the boundary edge in a given direction

    INPUT:
    label_verts: np.array - array of vertices in boundary
    direction: str - direction to search for first point inside boundary

    OUTPUT:
    first_vert_index: int - index of first vert inside boundary
    """
    if direction == 'anterior':
        dir_idx = 1
        dir_function = np.max
    elif direction == 'posterior':
        dir_idx = 1
        dir_function = np.min
    elif direction == 'inferior':
        dir_idx = 2
        dir_function = np.min
    elif direction == 'superior':
        dir_idx = 2
        dir_function = np.max

    first_point = dir_function(label_RAS[:, dir_idx])
    first_RAS = label_RAS[np.where(label_RAS[:, dir_idx] == first_point)]
    first_vert_index = label_ind[np.where(label_RAS[:, dir_idx] == first_point)]

    return np.array(first_vert_index), np.array(first_RAS)

In [ ]:

def get_vertices_in_bounded_area(all_faces, all_points, boundary_faces):
    """
    For a list of boundary faces, start at the most posterior node (node 1)

    find all adjacent faces, and select the faces with the most anterior node (node 2)

    Using the faces defined by node 1 and node 2, breadth first search until you encounter boundary faces and there are no more unvisited nodes

    INPUT:
    all_faces: np.array - array of faces in mesh
    all_points: np.array - array of points in mesh
    boundary_verts: np.array - array of boundary vertex indices

    OUTPUT:
    label_points: np.array - array of points in bounded area

    """
    # Get all points in boundary
    label_points = np.unique(boundary_faces)

    # Calculate adjacency matrix for traversal
    adj_mat = mesh_to_adjacency(all_faces, all_points)
    
    # return the index of the most posterior point in the boundary (idx in all_points)
    all_boundary_points = all_points[label_points]
    boundary_index = find_edge_vert(all_boundary_points, 'posterior')
            
    first_anterior_vertex = find_vert_inside(adjacency_matrix=adj_mat,
                                            vert=boundary_index,
                                            all_verts=all_points,
                                            label_verts=label_points,
                                            direction='anterior')

    # breadth first search from first anterior point, treating boundary points as end of the graph
    queue = [first_anterior_vertex]

    while queue:
        visited = label_points
        vertex = queue.pop(0)
        if vertex not in label_points:
            ## Seems infinite
            ## Not adding any points
            np.append(label_points, vertex)
            for adj in adjacenct_nodes(adj_mat, vertex):
                if adj not in visited:
                    queue.append(adj)
                    np.append(visited, adj)
    
    return label_points

label_points = points[np.unique(pos_boundary)]
min_val = np.min(label_points[:,1])
np.where(points[:,1] == min_val)[0][0]

#adj_mat = mesh_to_adjacency(faces, points)

#label_points = get_vertices_in_bounded_area(faces, points, pos_boundary)


31430

In [ ]:
# label_points = points[np.unique(pos_boundary)]
# min_val = np.min(label_points[:,1])
# np.where(points[:,1] == min_val)[0][0]

# adj_mat = mesh_to_adjacency(faces, points)

In [ ]:
# label_points = get_vertices_in_bounded_area(faces, points, pos_boundary)

     

In [15]:
def get_faces_from_vertices(faces : np.array, label_ind : np.array):
    """
    Takes a list of faces and label indices
    Returns the faces that contain the indices

    INPUT:
    faces: array of faces composed of 3 points
    label_ind: array of indices of points in the label (first colum of label file; 0 index in read_label)

    OUTPUT:
    label_faces: array of faces that contain the points in the label
    """
    all_label_faces = []
    for face in faces:
        for point_index in face:
            if point_index in label_ind:
                all_label_faces.append(list(face))
    return np.array(all_label_faces)

In [17]:
post_RAS, post_ind = get_verts_bounded(test_brain[0], test_lab[1], test_lab[0], label_faces)

NameError: name 'get_verts_bounded' is not defined

In [ ]:
test_lab[0]

NameError: name 'test_lab' is not defined

In [ ]:
import src.surface_funcs

In [ ]:
test_brain[0]

array([[-18.26587105, -83.14471436,  -9.24630356],
       [-18.45186424, -83.28675079,  -9.27944374],
       [-18.05605888, -83.37046814,  -9.62107277],
       ...,
       [ -3.6713028 ,  76.56999969, -34.52028275],
       [ -5.04430962,  78.30000305, -34.86407852],
       [ -7.03128386,  74.28708649, -35.66125107]])

In [ ]:
get_anterior_point(test_brain[0], test_lab[0])

(array([[-6.16030388e+01, -3.43686676e+01,  4.53817919e-02]]), array([36988]))

In [ ]:
def get_anterior_point(all_RAS, label_index):

    """
    """

    label_RAS = all_RAS[label_index]
    ant_RAS = label_RAS[np.argmin(label_RAS[:,1])]
    ant_ind = np.where((all_RAS == ant_RAS).all(axis = 1))[0]
    return np.array([ant_RAS]), ant_ind


In [ ]:
ant_point

label_ind = np.where((test_brain[0] == ant_point).all(axis = 1))[0]
label_ind[0]

36988

In [ ]:
np.array([post_RAS])[0]

array([-65.27854156, -36.50906754,  -0.93585503])

In [73]:
sfu.write_label(label_ind, np.array([ant_point]), "ant_point_csts1", "lh", "/Users/sathishkumar/Desktop/", overwrite=True)

NameError: name 'ant_point' is not defined

In [ ]:
label_ind = np.where((test_brain[0] == post_RAS).all(axis = 1))[0]
label_ind

array([37004])

In [ ]:
np.array([post_ind])

array([37004], dtype=int32)

In [74]:
sfu.write_label(np.array([post_ind]), np.array([post_RAS]), "post_point_csts1", "lh", "/Users/sathishkumar/Desktop/", overwrite=True)

Writing label lh.post_point_csts1.label for Desktop


In [ ]:
import nibabel as nib
from src import freesurfer_utils as fsu

test_lab = fsu.read_label(f"{subjects_dir}/c05/label/lh.csts-1.label")
test_brain = nib.freesurfer.read_geometry(f"{subjects_dir}/c05/surf/lh.pial")

TypeError: isinstance expected 2 arguments, got 1

In [ ]:
import sys
project_path = os.path.abspath(os.path.join('..'))
if project_path not in sys.path:
    sys.path.insert(0, project_path)
print(sys.path)

['/Users/sathishkumar/Desktop/lab.nosync/CNL_scalpel', '/Users/sathishkumar/Desktop/lab.nosync/CNL_scalpel/src', '/Users/sathishkumar/Desktop/lab.nosync/CNL_scalpel/src', '../src', '../src', '/Users/sathishkumar/Desktop/lab.nosync/CNL_scalpel/notebooks', '/Library/Frameworks/Python.framework/Versions/3.11/lib/python311.zip', '/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11', '/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/lib-dynload', '', '/Users/sathishkumar/Library/Python/3.11/lib/python/site-packages', '/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages']


In [ ]:
def find_adjacent(faces):
    """
    INPUT:
        
    OUTPUT:
        list of indices of the adjacent points
    """

In [73]:
len(roi_boundary_points)

1581

In [111]:
roi_mesh = tm.Trimesh(vertices= points, faces = roi_boundary_faces)
roi_mesh.show()

In [99]:
def get_first_interior_point(all_RAS, roi_boundary_faces, roi_boundary_ind, ant_label_faces, ant_label_ind, all_faces, whole_brain_graph):
    """
    INPUT
    all_RAS: all_RAS coordinates
    roi_boundary_faces: faces that boundaries to the ROI
    roi_boundary_ind: inds that are boundaries to the ROI
    ant_label_inds: indices of anterior label
    all_faces: all faces on brain
    whole_brain_graph: graph representation of whole brain

    OUTPUT: first point (anterior to the posterior point) that is within the label.
    """

    #finding most anterior point    
    posterior_ind, posterior_RAS = find_edge_vert(all_RAS[ant_label_ind], ant_label_ind, "posterior")
    print(posterior_RAS, posterior_ind)
    index_in_label = True

    #searches adjacent nodes to find vert not in label
    current_ind = posterior_ind
    while index_in_label:
        print("running")
        adj_inds = list(whole_brain_graph.neighbors(current_ind))
        adj_RAS = {adj_ind : all_RAS[adj_ind] for adj_ind in adj_inds}
        sorted_data = sorted(adj_RAS.items(), key=lambda x: x[1][1], reverse=True) 
        sorted_dict = {k: v for k, v in sorted_data}

        #adj_inds = np.unique([adj_node for adj_node in label_faces if current_ind in adj_node])
        #adj_RAS = {adj_ind : all_RAS[adj_ind] for adj_ind in adj_inds}
        #sorted_data = sorted(adj_RAS.items(), key=lambda x: x[1][1]) 
        #sorted_dict = {k: v for k, v in sorted_data}

        new_anterior_ind = list(sorted_dict.keys())[0]
        current_ind = new_anterior_ind

        if not current_ind in r:
            index_in_label = False
            break
    
    ant_RAS = all_RAS[current_ind]

    return ant_RAS, current_ind

In [101]:
fsu.write_label(np.array([post_ind]), np.array([post_RAS]), "ant_point_slos-v", "lh", "/Users/sathishkumar/Desktop/", overwrite=True)

Writing label lh.ant_point_slos-v.label for Desktop


In [ ]:
fsu.write_label(np.array([post_ind]), np.array([post_RAS]), "post_point_csts1", "lh", "/Users/sathishkumar/Desktop/", overwrite=True)

In [60]:
whole_brain_graph = create_graph_from_mesh(points, faces)
label_ind, label_RAS = read_label(f'{subjects_dir}/{sub}/label/lh.slos-v.label')
posterior_label_ind = label_ind
post_RAS, post_ind = get_first_interior_point(points, label_RAS, posterior_label_ind, label_faces, faces, whole_brain_graph)



[[-55.551 -43.939  12.423]] [25502]
running
running
running
running
running
running
running
running
running
running
running
running
running


In [80]:
def make_roi_cut(anterior: str, posterior: str, superior: str, inferior: str, hemi: str, all_points: np.array, all_faces: np.array, subjects_dir: str or Path, sub: str):
    """ 
    Create an outlined region of cortex, using each of the labels as the boundary in a given direction. Take 4 labels names, hemisphere, and mesh, and create a single label that is the bounded roi.

    INPUT: 
    anterior: str - name of anterior label
    posterior: str - name of posterior label
    superior: str - name of superior label
    inferior: str - name of inferior label
    hemi: str - hemisphere of interest
    all_points: np.array - array of all points in a hemisphere as loaded by nibabel freesurfer.io.read_geometry
    all_faces: np.array - array of all faces in a hemisphere as loaded by nibabel freesurfer.io.read_geometry
    subjects_dir: str or Path - path to freesurfer subjects directory
    sub: str - subject id

    OUTPUT:
    roi_label_ind: np.array - array of indices of vertices in the bounded roi
    roi_label_points: np.array - array of points in the bounded roi

    
    """


    labels = {'anterior': [anterior], 'posterior': [posterior], 'superior': [superior], 'inferior': [inferior]}

    for i in labels.keys():
        labels[i].append(sfu.read_label(f'{subjects_dir}/{sub}/label/{hemi}.{labels[i][0]}.label'))

    edge_points = {}

    ## Get edge points for each boundary label
    for boundary in labels.keys():
        if boundary == 'anterior' or boundary == 'posterior':
            edges = ['superior', 'inferior']
            label_ind = labels[boundary][1][0]
            label_RAS = labels[boundary][1][1]
            label_name = labels[boundary][0]
            edge_points[f'{boundary}_{label_name}_label_{edges[0]}_edge'] = find_edge_vert(label_RAS, label_ind, edges[0])
            edge_points[f'{boundary}_{label_name}_label_{edges[1]}_edge'] = find_edge_vert(label_RAS, label_ind, edges[1])

        else:
            edges = ['anterior', 'posterior']
            label_ind = labels[boundary][1][0]
            label_RAS = labels[boundary][1][1]
            label_name = labels[boundary][0]
            edge_points[f'{boundary}_{label_name}_label_{edges[0]}_edge'] = find_edge_vert(label_RAS, label_ind, edges[0])
            edge_points[f'{boundary}_{label_name}_label_{edges[1]}_edge'] = find_edge_vert(label_RAS, label_ind, edges[1])

    ## Get the shortest path between the paired points on the boundary
    boundary_paths = {}

    for ant_post in ["anterior", "posterior"]:
        for sup_inf in ["superior", "inferior"]:
            starting_vertex = edge_points[f"{ant_post}_{labels[ant_post][0]}_label_{sup_inf}_edge"][0][0]
            target_vertex = edge_points[f"{sup_inf}_{labels[sup_inf][0]}_label_{ant_post}_edge"][0][0]

            path = find_shortest_path_in_mesh(all_points, all_faces, starting_vertex, target_vertex)
            boundary_faces = get_faces_from_vertices(all_faces, path)
            boundary_paths[f"{ant_post}_{sup_inf}_{labels[ant_post][0]}_to_{sup_inf}_{ant_post}_{labels[sup_inf][0]}"] = path
            #boundary_paths[f"{ant_post}_{sup_inf}_{labels[ant_post][0]}_to_{sup_inf}_{ant_post}_{labels[sup_inf][0]}"] = boundary_faces

    ## Combine all labels and paths into a single label
    
    roi_label_ind = np.unique(np.concatenate([labels[i][1][0] for i in labels.keys()]))
    print(len(roi_label_ind))
    for i in boundary_paths.keys():
        print(boundary_paths[i])
        roi_label_ind = np.unique(np.concatenate([roi_label_ind, boundary_paths[i]], axis=None))
        print(len(roi_label_ind))
    roi_label_points = all_points[roi_label_ind]
    return [roi_label_ind, roi_label_points]

In [81]:
def get_roi(roi_boundary_RAS: np.array, roi_boundary_ind: np.array, anterior_label_ind: np.array, all_RAS: np.array, all_faces: np.array, label_faces: np.array, inclusive = False):

    # might change name to roi_boundary_faces instead of label_faces to be more clear

    """
    INPUT:
    -------
    roi_boundary: points that are on the boundary for the roi
    all_RAS: dictionary containing all points on surface

    OUTPUT:
    ROI_indices: 
    -------
    
    """
    
    # create graph
    whole_brain_graph = create_graph_from_mesh(all_RAS, all_faces)

    #find the anterior label
oi
    # next get the first interior point
    interior_RAS, interior_ind = get_first_interior_point(all_RAS, roi_boundary_RAS, roi_boundary_ind, label_faces, all_faces, whole_brain_graph)

    # BFS from the interior point
    adj_inds = whole_brain_graph.neighbors(interior_ind)
    # adj_inds = np.unique([adj_node for adj_node in all_faces if interior_point in adj_node])
    # adj_RAS = {adj_ind : all_RAS[adj_ind] for adj_ind in adj_inds} #not sure if i need this yet
    indices_queue = adj_inds
    ROI_indices = np.array([interior_ind])

    while (indices_queue.size > 0):
        curr_index = indices_queue.pop(0)
        ROI_indices = np.concatenate(ROI_indices, curr_index)
        if curr_index not in roi_boundary_ind:
            new_adj_indices = whole_brain_graph.neighbors(curr_index)
            indices_queue = np.concatenate(indices_queue, new_adj_indices)
    
    if (inclusive):
        np.append(ROI_indices, roi_boundary_ind)
    return ROI_indices

In [95]:
anterior, posterior, superior, inferior = ['smgs', 'slos-v', 'aipsj', 'csts-1']
# brain is currently lh c05
roi_boundary_ind, roi_boundary_points = make_roi_cut(anterior, posterior, superior, inferior, hemi, points, faces, subjects_dir, sub)
roi_boundary_faces = get_boundary_faces(faces, roi_boundary_ind)

1665
[54677, 53587, 52518, 51416, 50378, 49364, 48357, 47195, 46171, 45087, 43964, 42760, 41631, 41621, 40592, 39607, 38650, 37692, 36684, 35634, 35633, 34643]
1683
[43056, 41917, 40877, 39901, 38916, 37953, 36931, 36915, 35884, 35897, 36928, 36945, 37983, 38948, 39915, 39914, 40890, 41933, 43073, 43083, 44297, 44296, 45362, 45374, 46402, 46415]
1690
[40671, 39707, 38754, 37787, 37788, 36760, 35721, 34720, 33765, 32812, 32811, 31866, 31865, 30906, 30905, 30885, 30007, 29986, 29966, 29112, 28251, 27307]
1696
[39936, 39935, 40899, 41941, 43068, 44273, 44274, 44275, 44276, 44258, 44259, 44260, 44261, 44262, 43050, 43051, 41911, 41912, 40872, 40873, 39896, 39897, 38935, 37970, 37971, 36928, 36946, 36958, 36971, 36988]
1708


In [97]:
boundary_mesh = tm.Trimesh(vertices=points, faces =roi_boundary_faces)
boundary_mesh.show()

In [98]:
get_roi(roi_boundary_points, roi_boundary_ind, points, faces, label_faces, whole_brain_graph)

TypeError: tuple indices must be integers or slices, not tuple

In [90]:
def graph_from_mesh(mesh):
    brain_graph = ig.Graph(mesh.vertices.shape, edges = mesh.edges_unique)
    return brain_graph

test_graph = graph_from_mesh(mesh)

In [4]:
import src.freesurfer_utils as fsu
fsu.write_label(roi_faces, roi_points, 'roi_IPS_csts-1_aipsj_smgs', 'lh', subject_dir = '/Users/sathishkumar/Desktop/chimp_subjects.nosync/results', overwrite = True)

NameError: name 'roi_faces' is not defined